In [4]:
!nvidia-smi

zsh:1: command not found: nvidia-smi


In [5]:
!git clone https://github.com/tloen/alpaca-lora.git

Cloning into 'alpaca-lora'...
remote: Enumerating objects: 607, done.
remote: Counting objects: 100% (51/51), done.
remote: Compressing objects: 100% (32/32), done.
remote: Total 607 (delta 28), reused 34 (delta 19), pack-reused 556
Receiving objects: 100% (607/607), 27.78 MiB | 4.33 MiB/s, done.
Resolving deltas: 100% (360/360), done.


# Alpaca LLaMa 7B LoRa

In [6]:
%cd alpaca-lora/

/Users/dano/DEV/smartscraper/smartscraper/alpaca-lora


In [ ]:
!pip install -q datasets loralib sentencepiece

!pip uninstall -y transformers
!pip install -q git+https://github.com/zphang/transformers@c3dc391
# pip install git+https://github.com/zphang/transformers.git@llama_push

!pip install -q git+https://github.com/huggingface/peft.git

In [5]:
!pip install bitsandbytes

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.3/104.3 MB 9.8 MB/s eta 0:00:00


## Data Check

In [6]:
from datasets import load_dataset
from transformers import LLaMATokenizer


tokenizer = LLaMATokenizer.from_pretrained("decapoda-research/llama-7b-hf", add_eos_token=True)
tokenizer.pad_token = tokenizer.eos_token
tokenizer.pad_token_id = tokenizer.eos_token_id

data = load_dataset("json", data_files="alpaca_data.json")


def generate_prompt(data_point):
    # sorry about the formatting disaster gotta move fast
    if data_point["input"]:
        return f"""
### Instruction:
{data_point["instruction"]}

### Input:
{data_point["input"]}

### Response:
{data_point["output"]}"""
    else:
        return f"""
### Instruction:
{data_point["instruction"]}

### Response:
{data_point["output"]}"""


data = data.map(lambda data_point: {"prompt": tokenizer(generate_prompt(data_point))})

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Dataset json downloaded and prepared to /root/.cache/huggingface/datasets/json/default-8b6abf24a2251c59/0.0.0/fe5dd6ea2639a6df622901539cb550cf8797e5a6b2dd7af1cf934bed8e233e6e. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

Map:   0%|          | 0/52002 [00:00<?, ? examples/s]

## Fine Tuning

In [ ]:
from google.colab import files
uploaded = files.upload()

Saving samples.json to samples.json


In [ ]:
!conda install -y -c conda-forge cudatoolkit

In [ ]:
# import os

# # Set PATH variable
# cuda_path = "/usr/local/cuda/bin"  # Update this to the correct path on your system
# os.environ["PATH"] = f"{cuda_path}:{os.environ['PATH']}"

# # Set LD_LIBRARY_PATH variable
# cuda_lib_path = "/usr/local/cuda/lib64"  # Update this to the correct path on your system
# os.environ["LD_LIBRARY_PATH"] = f"{cuda_lib_path}:{os.environ.get('LD_LIBRARY_PATH', '')}"

In [ ]:
# !cp /opt/conda/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda117.so /opt/conda/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cpu.so

In [7]:
import os

# os.environ["CUDA_VISIBLE_DEVICES"] = "0"
import torch
import torch.nn as nn
import bitsandbytes as bnb
from datasets import load_dataset
import transformers
from transformers import AutoTokenizer, AutoConfig, LLaMAForCausalLM, LLaMATokenizer
from peft import prepare_model_for_int8_training, LoraConfig, get_peft_model


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /usr/local/lib/python3.9/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 118
CUDA SETUP: Loading binary /usr/local/lib/python3.9/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so...


/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: /usr/lib64-nvidia did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/sys/fs/cgroup/memory.events /var/colab/cgroup/jupyter-children/memory.events')}
  warn(msg)
/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('http'), PosixPath('8013'), PosixPath('//172.28.0.1')}
  warn(msg)
/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('//colab.research.google.com/tun/m/cc48301118ce

In [8]:
# Setting for A100 - For 3090 
MICRO_BATCH_SIZE = 8  # change to 4 for 3090
BATCH_SIZE = 128
GRADIENT_ACCUMULATION_STEPS = BATCH_SIZE // MICRO_BATCH_SIZE
EPOCHS = 2  # paper uses 3
LEARNING_RATE = 2e-5  # from the original paper
LORA_R = 4
LORA_ALPHA = 16
LORA_DROPOUT = 0.05

In [9]:
model = LLaMAForCausalLM.from_pretrained(
    "decapoda-research/llama-7b-hf",
    load_in_8bit=True,
    device_map="auto",
)
tokenizer = LLaMATokenizer.from_pretrained(
    "decapoda-research/llama-7b-hf", add_eos_token=True
)

model = prepare_model_for_int8_training(model)


Overriding torch_dtype=None with `torch_dtype=torch.float16` due to requirements of `bitsandbytes` to enable model loading in mixed int8. Either pass torch_dtype=torch.float16 or don't pass this argument at all to remove this warning.


Loading checkpoint shards:   0%|          | 0/33 [00:00<?, ?it/s]

In [11]:
config = LoraConfig(
    r=LORA_R,
    lora_alpha=LORA_ALPHA,
    target_modules=["q_proj", "v_proj"],
    lora_dropout=LORA_DROPOUT,
    bias="none",
    task_type="CAUSAL_LM",
)
model = get_peft_model(model, config)
tokenizer.pad_token_id = 0  # unk. we want this to be different from the eos token
data = load_dataset("json", data_files="samples.json")


In [18]:
torch.cuda.empty_cache()
!nvidia-smi

/bin/bash: nvidia-smi: command not found


In [ ]:

def generate_prompt(data_point):
    # sorry about the formatting disaster gotta move fast
    if data_point["input"]:
        return f"""### Instruction:
{data_point["instruction"]}
### Input:
{data_point["input"]}
### Response:
{data_point["output"]}"""
    else:
        return f"""### Instruction:
{data_point["instruction"]}
### Response:
{data_point["output"]}"""


data = data.shuffle().map(
    lambda data_point: tokenizer(
        generate_prompt(data_point),
        truncation=False,
        padding='longest',
    )
)


trainer = transformers.Trainer(
    model=model,
    train_dataset=data["train"],
    args=transformers.TrainingArguments(
        per_device_train_batch_size=MICRO_BATCH_SIZE,
        gradient_accumulation_steps=GRADIENT_ACCUMULATION_STEPS,
        warmup_steps=100,
        num_train_epochs=EPOCHS,
        learning_rate=LEARNING_RATE,
        fp16=True,
        logging_steps=1,
        output_dir="lora-smartscraper",
        save_total_limit=3,
    ),
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)
model.config.use_cache = False
trainer.train(resume_from_checkpoint=False)

model.save_pretrained("lora-smartscraper")

Map:   0%|          | 0/10000 [00:00<?, ? examples/s]

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <cell line: 46>:46                                                                            │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/transformers/trainer.py:1628 in train                     │
│                                                                                                  │
│   1625 │   │   inner_training_loop = find_executable_batch_size(                                 │
│   1626 │   │   │   self._inner_training_loop, self._train_batch_size, args.auto_find_batch_size  │
│   1627 │   │   )                                                                                 │
│ ❱ 1628 │   │   return inner_training_loop(                                                       │
│   1629 │   │   │   args=args,                                                                    │
│   1630 │   │   │   resume_from_checkpoint=resume_from_checkpoint,                                │
│   1631 │   │   │   trial=trial,                                                                  │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/transformers/trainer.py:1895 in _inner_training_loop      │
│                                                                                                  │
│   1892 │   │   │   │   │   with model.no_sync():                                                 │
│   1893 │   │   │   │   │   │   tr_loss_step = self.training_step(model, inputs)                  │
│   1894 │   │   │   │   else:                                                                     │
│ ❱ 1895 │   │   │   │   │   tr_loss_step = self.training_step(model, inputs)                      │
│   1896 │   │   │   │                                                                             │
│   1897 │   │   │   │   if (                                                                      │
│   1898 │   │   │   │   │   args.logging_nan_inf_filter                                           │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/transformers/trainer.py:2647 in training_step             │
│                                                                                                  │
│   2644 │   │   │   loss = loss / self.args.gradient_accumulation_steps                           │
│   2645 │   │                                                                                     │
│   2646 │   │   if self.do_grad_scaling:                                                          │
│ ❱ 2647 │   │   │   self.scaler.scale(loss).backward()                                            │
│   2648 │   │   elif self.use_apex:                                                               │
│   2649 │   │   │   with amp.scale_loss(loss, self.optimizer) as scaled_loss:                     │
│   2650 │   │   │   │   scaled_loss.backward()                                                    │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/torch/_tensor.py:487 in backward                          │
│                                                                                                  │
│    484 │   │   │   │   create_graph=create_graph,                                                │
│    485 │   │   │   │   inputs=inputs,                                                            │
│    486 │   │   │   )                                                                             │
│ ❱  487 │   │   torch.autograd.backward(                                                          │
│    488 │   │   │   self, gradient, retain_graph, create_gra

In [ ]:
from huggingface_hub import notebook_login

notebook_login()

Token is valid.
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [ ]:
model.push_to_hub("DDDano333/smartscraper", use_auth_token=True)

adapter_model.bin:   0%|          | 0.00/8.43M [00:00<?, ?B/s]

Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

CommitInfo(commit_url='https://huggingface.co/DDDano333/smartscraper/commit/83a671b384ebf41ac421507590596c2d3da11789', commit_message='Upload model', commit_description='', oid='83a671b384ebf41ac421507590596c2d3da11789', pr_url=None, pr_revision=None, pr_num=None)

## Generation

In [ ]:
torch.cuda.empty_cache()

In [15]:
from peft import PeftModel
from transformers import LLaMATokenizer, LLaMAForCausalLM, GenerationConfig

tokenizer = LLaMATokenizer.from_pretrained("decapoda-research/llama-7b-hf")

model = LLaMAForCausalLM.from_pretrained(
    "decapoda-research/llama-7b-hf",
    load_in_8bit=True,
    device_map="auto",
)
model = PeftModel.from_pretrained(model, "DDDano333/smartscraper")
# model = get_peft_model(model, config)

PROMPT = """### Below is an instruction that describes a task. Write a response that appropriately completes the request.
### Instruction: Please parse the given text and extract the ticket information. Create a list of dictionaries, where each dictionary represents a single ticket and contains the following keys: 'ticket_number', 'court', 'agency', 'violation_date', and 'status'. Convert the extracted information into the appropriate format and output the resulting list of dictionaries.
### Input: [Header]Traffic Ticket Information Center\nTicket Resolution Process:\nI.User Terms of Service\nII.Fetch Ticket Information\nIII.Online Citation Options\nIV.Fee and Appointment\nV.Approval\nDL Number: MZQ 834\nDate of Birth: 03/24/1939\nClick on Ticket Number for more details.\nTicket NumberCourtLaw Enforcement AgencyViolation DateStatus\n\n2566466Jonesview Legal ComplexGoodman PLC04-12-2023Appeal Granted\n2313665Michaelfurt Courthouse AnnexWalton-Arnold02 23 2023Continuance Granted\n9033403East Troyville Tribunal HousePowell, Shields and Daniel03/24/2023Court Date Set\n4588574Robertsside Court FacilityLarson Group03-07-2023Reopened\n7064063Teresamouth Court ChambersLi LLC01/09/2023Appeal Granted\n5195664New Timothy Tribunal HouseKane-Sanders02-12-2023Appeal Filed\n5435899Cynthiaport Judiciary PremisesFisher-Maxwell04-03-2023Sentenced\n6667788Miguelborough Court CenterTorres, Harrison and Bishop01/19/2023Guilty\n[Warnings and Instructions]\nBe aware that it can take up to 30 days for traffic tickets to be posted online. If you're unable to find your ticket after this period, reach out to the law enforcement agency that issued the ticket. You are still required to address your ticket before the deadline, even if it's not available online. If you've already reached out to the agency and your ticket is still not online, visit the courthouse listed on your ticket by the due date. Remember, neglecting to handle your ticket in a timely manner may result in penalties.
### Response:"""

inputs = tokenizer(
    PROMPT,
    return_tensors="pt",
)
input_ids = inputs["input_ids"].cuda()

generation_config = GenerationConfig(
    temperature=0.6,
    top_p=0.95,
    repetition_penalty=1.15,
)
print("Generating...")
generation_output = model.generate(
    input_ids=input_ids,
    generation_config=generation_config,
    return_dict_in_generate=True,
    output_scores=True,
    max_new_tokens=128,
)
for s in generation_output.sequences:
    print(tokenizer.decode(s))

Overriding torch_dtype=None with `torch_dtype=torch.float16` due to requirements of `bitsandbytes` to enable model loading in mixed int8. Either pass torch_dtype=torch.float16 or don't pass this argument at all to remove this warning.


╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <cell line: 6>:6                                                                              │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/transformers/modeling_utils.py:2578 in from_pretrained    │
│                                                                                                  │
│   2575 │   │   │   │   │   key: device_map[key] for key in device_map.keys() if key not in modu  │
│   2576 │   │   │   │   }                                                                         │
│   2577 │   │   │   │   if "cpu" in device_map_without_lm_head.values() or "disk" in device_map_  │
│ ❱ 2578 │   │   │   │   │   raise ValueError(                                                     │
│   2579 │   │   │   │   │   │   """                                                               │
│   2580 │   │   │   │   │   │   Some modules are dispatched on the CPU or the disk. Make sure yo  │
│   2581 │   │   │   │   │   │   the quantized model. If you have set a value for `max_memory` yo  │
╰──────────────────────────────────────────────────────────────────────────────────────────────────╯
ValueError: 
                        Some modules are dispatched on the CPU or the disk. Make sure you have enough GPU RAM to 
fit
                        the quantized model. If you have set a value for `max_memory` you should increase that. To 
have
                        an idea of the modules that are set on the CPU or RAM you can print model.hf_device_map.

In [ ]:
PROMPT ='''### instruction: Please parse the given text and extract the ticket information. Create a list of dictionaries, where each dictionary represents a single ticket and contains the following keys: 'ticket_number', 'court', 'agency', 'violation_date', and 'status'. Convert the extracted information into the appropriate format and output the resulting list of dictionaries.
### input: [Header]Traffic Ticket Status\nTicket Resolution Steps:\n- Terms of Use\n- Obtain Ticket Info\n- Internet Ticket Alternatives\n- Payment and Booking\n- Acknowledgment\n\nDL Number: 3800 YQ\nBirth Date: 11/02/1987\n\nClick the Ticket Number for more information.\n\nTicket NumberCourtLaw Enforcement AgencyViolation DateStatus\n\n7833537West Karen Tribunal HouseEllis-Calderon03 01 2023Appeal Filed\n1517406Johnland Judicial BuildingElliott Group03-01-2023Reopened\n5508653Longbury Judicial CenterNguyen-Holmes02/24/2023Extension\n8926090Lake Mark Court FacilityWarner Inc03-07-2023Adjourned\nMake sure to review your ticket information before proceeding.
'''

In [ ]:
%%time

inputs = tokenizer(
    PROMPT,
    return_tensors="pt",
)
input_ids = inputs["input_ids"].cuda()

generation_config = GenerationConfig(
    temperature=0.6,
    top_p=0.95,
    repetition_penalty=1.15,
)
print("Generating...")
generation_output = model.generate(
    input_ids=input_ids,
    generation_config=generation_config,
    return_dict_in_generate=True,
    output_scores=True,
    max_new_tokens=128,
)
for s in generation_output.sequences:
    print(tokenizer.decode(s))

Generating...


╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ /usr/local/lib/python3.9/dist-packages/IPython/core/magics/execution.py:1335 in time             │
│                                                                                                  │
│   1332 │   │   else:                                                                             │
│   1333 │   │   │   st = clock2()                                                                 │
│   1334 │   │   │   try:                                                                          │
│ ❱ 1335 │   │   │   │   exec(code, glob, local_ns)                                                │
│   1336 │   │   │   │   out=None                                                                  │
│   1337 │   │   │   │   # multi-line %%time case                                                  │
│   1338 │   │   │   │   if expr_val is not None:                                                  │
│ in <module>:13                                                                                   │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/peft/peft_model.py:721 in generate                        │
│                                                                                                  │
│    718 │   │   self.base_model.prepare_inputs_for_generation = self.prepare_inputs_for_generati  │
│    719 │   │   try:                                                                              │
│    720 │   │   │   if not isinstance(peft_config, PromptLearningConfig):                         │
│ ❱  721 │   │   │   │   outputs = self.base_model.generate(**kwargs)                              │
│    722 │   │   │   else:                                                                         │
│    723 │   │   │   │   if "input_ids" not in kwargs:                                             │
│    724 │   │   │   │   │   raise ValueError("input_ids must be provided for Peft model generati  │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/torch/utils/_contextlib.py:115 in decorate_context        │
│                                                                                                  │
│   112 │   @functools.wraps(func)                                                                 │
│   113 │   def decorate_context(*args, **kwargs):                                                 │
│   114 │   │   with ctx_factory():                                                                │
│ ❱ 115 │   │   │   return func(*args, **kwargs)                                                   │
│   116 │                                                                                          │
│   117 │   return decorate_context                                                                │
│   118                                                                                            │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/transformers/generation/utils.py:1406 in generate         │
│                                                                                                  │
│   1403 │   │   │   │   )                                                                         │
│   1404 │   │   │                                                                                 │
│   1405 │   │   │   # 11. run greedy search                                                       │
│ ❱ 1406 │   │   │   return self.greedy_search(                                                    │
│   1407 │   │   │   │   input_ids,                                                                │
│   1408 │   │   │   │   logits_processor=logits_processor,  

In [ ]:
import math


def is_prime(number):  # Checks if a given integer is a prime number.
    for i in range (2, int(math.ceil(math.sqrt(number)))+1):
        if number % i == 0:
            return False
    return True

In [ ]:
is_prime(23)

True